In [1]:
# save_path='/root/gudongzhou/LIGHTEN-Learning-Interactions-with-Graphs-and-Hierarchical-TEmporal-Networks-for-HOI-master/V-COCO/output/gdz_vcoco_test_scores.pkl'
# vcocoeval = VCOCOeval('/root/gudongzhou/PPDM0102V2.0/src/gdz_util/anno/vcoco_test.json', '/root/gudongzhou/PPDM0102V2.0/src/gdz_util/anno/instances_vcoco_all_2014.json', '/root/gudongzhou/PPDM0102V2.0/src/gdz_util/anno/vcoco_test.ids')
# vcocoeval._do_eval(save_path, ovr_thresh=0.5)

In [2]:
import numpy as np
from pycocotools.coco import COCO
import json
import copy
# import cPickle as pickle
import pickle as pickle

In [3]:
vsrl_annot_file='/root/gudongzhou/PPDM0102V2.0/src/gdz_util/data/vcoco/vcoco_test.json'
coco_annot_file='/root/gudongzhou/PPDM0102V2.0/src/gdz_util/anno/instances_vcoco_all_2014.json'
split_file='/root/gudongzhou/PPDM0102V2.0/src/gdz_util/data/vcoco/vcoco_test.ids'

In [4]:
COCO = COCO(coco_annot_file)

loading annotations into memory...
Done (t=1.80s)
creating index...
index created!


In [5]:
print('loading vcoco annotations...')

loading vcoco annotations...


In [6]:
vcoco_file=vsrl_annot_file
with open(vcoco_file, 'r') as f:
    vsrl_data = json.load(f)

## 通过下面对vcoco_test.json的分析得出

 该标签文件由26个动作组成，json长度为26
 每个动作标签含有以下字段：dict_keys(['image_id', 'ann_id', 'role_object_id', 'label', 'action_name', 'role_name', 'include'])
1. 'image_id'长度为7768，去重后为4946，也就是所有图片的数量；说明image_id标注的是测试集中所有person的数量的7768，使用image_id来标记person在那个image
2. 'ann_id'长度为7768，去重后长度为7768，每个person对应的标注id
3. 'role_object_id'长度为15536=7768*2，代表person+object)
4. 'label'的长度为7768，值为1或0，代表7768个person是否在执行此action
5. 'action_name'代表这个标签的动作，为26种动作中的一个
6. 'role_name'有以下几种可能，代表该action_name可能发生的交互类型,其中walk，smile,run，stand四种动作对应 ['agent']；
['agent', 'obj'],
 ['agent'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent', 'instr', 'obj'],
 ['agent', 'obj', 'instr']
 

In [7]:
len(vsrl_data)

26

In [8]:
len(vsrl_data[0]['image_id'])

7768

In [9]:
len(np.unique(vsrl_data[0]['image_id']))

4946

In [84]:
vsrl_data[0]['role_object_id']

array([[ 183014,       0],
       [ 183062,       0],
       [ 183100, 2112209],
       ...,
       [2229301,       0],
       [2229367,  629756],
       [2229495,       0]])

In [10]:
vsrl_data[0].keys()

dict_keys(['image_id', 'ann_id', 'role_object_id', 'label', 'action_name', 'role_name', 'include'])

In [11]:
len(vsrl_data[0]['ann_id'])

7768

In [12]:
len(np.unique(vsrl_data[0]['ann_id']))

7768

In [13]:
len(vsrl_data[0]['label'])

7768

In [14]:
len(vsrl_data[0]['role_name'])

2

In [15]:
vsrl_data[0]['role_name']

['agent', 'obj']

In [16]:
len(vsrl_data[0]['role_object_id'])

15536

In [17]:
len(np.unique(vsrl_data[0]['role_object_id']))

10424

In [18]:
for i in range(len(vsrl_data)):
    vsrl_data[i]['role_object_id'] = \
        np.array(vsrl_data[i]['role_object_id']).reshape((len(vsrl_data[i]['role_name']), -1)).T
    for j in ['ann_id', 'label', 'image_id']:
        vsrl_data[i][j] = np.array(vsrl_data[i][j]).reshape((-1, 1))

In [19]:
vsrl_data

[{'image_id': array([[ 45687],
         [209468],
         [293221],
         ...,
         [222468],
         [450845],
         [515854]]),
  'ann_id': array([[ 183014],
         [ 183062],
         [ 183100],
         ...,
         [2229301],
         [2229367],
         [2229495]]),
  'role_object_id': array([[ 183014,       0],
         [ 183062,       0],
         [ 183100, 2112209],
         ...,
         [2229301,       0],
         [2229367,  629756],
         [2229495,       0]]),
  'label': array([[0],
         [0],
         [1],
         ...,
         [0],
         [1],
         [1]]),
  'action_name': 'hold',
  'role_name': ['agent', 'obj'],
  'include': [[], []]},
 {'image_id': array([[ 45687],
         [209468],
         [293221],
         ...,
         [222468],
         [450845],
         [515854]]),
  'ann_id': array([[ 183014],
         [ 183062],
         [ 183100],
         ...,
         [2229301],
         [2229367],
         [2229495]]),
  'role_object_id': array

In [20]:
x=vsrl_data[8]
x

{'image_id': array([[ 45687],
        [209468],
        [293221],
        ...,
        [222468],
        [450845],
        [515854]]),
 'ann_id': array([[ 183014],
        [ 183062],
        [ 183100],
        ...,
        [2229301],
        [2229367],
        [2229495]]),
 'role_object_id': array([[ 183014,       0],
        [ 183062,       0],
        [ 183100,       0],
        ...,
        [2229301,       0],
        [2229367,       0],
        [2229495,       0]]),
 'label': array([[0],
        [0],
        [0],
        ...,
        [0],
        [0],
        [0]]),
 'action_name': 'jump',
 'role_name': ['agent', 'instr'],
 'include': [[], ['snowboard', 'skis', 'skateboard', 'surfboard']]}

In [21]:
x['label'].shape

(7768, 1)

In [22]:
has_label=np.where(x['label']==1)[0]

has_label.shape

(635,)

In [23]:
rids = x['role_object_id'][has_label]
rids[0]

array([185172, 640284])

In [24]:
a=0
b=0
for rid in rids:
    if rid[1] == 0:
        # no role
        a+=1
    else:
        b+=1

In [25]:
a


233

In [26]:
b

402

In [27]:
vsrl_data[0].keys()

dict_keys(['image_id', 'ann_id', 'role_object_id', 'label', 'action_name', 'role_name', 'include'])

In [28]:
vsrl_data[0]['role_object_id'].shape

(7768, 2)

In [29]:
VCOCO=vsrl_data

In [30]:
image_ids = np.loadtxt(open(split_file, 'r'))

In [31]:
image_ids.size

4946

## self._init_coco()


In [32]:
category_ids=COCO.getCatIds()
len(category_ids)

80

In [33]:
categories = [c['name'] for c in COCO.loadCats(category_ids)]

In [34]:
category_to_id_map = dict(zip(categories, category_ids))
category_to_id_map

{'person': 1,
 'bicycle': 2,
 'car': 3,
 'motorcycle': 4,
 'airplane': 5,
 'bus': 6,
 'train': 7,
 'truck': 8,
 'boat': 9,
 'traffic light': 10,
 'fire hydrant': 11,
 'stop sign': 13,
 'parking meter': 14,
 'bench': 15,
 'bird': 16,
 'cat': 17,
 'dog': 18,
 'horse': 19,
 'sheep': 20,
 'cow': 21,
 'elephant': 22,
 'bear': 23,
 'zebra': 24,
 'giraffe': 25,
 'backpack': 27,
 'umbrella': 28,
 'handbag': 31,
 'tie': 32,
 'suitcase': 33,
 'frisbee': 34,
 'skis': 35,
 'snowboard': 36,
 'sports ball': 37,
 'kite': 38,
 'baseball bat': 39,
 'baseball glove': 40,
 'skateboard': 41,
 'surfboard': 42,
 'tennis racket': 43,
 'bottle': 44,
 'wine glass': 46,
 'cup': 47,
 'fork': 48,
 'knife': 49,
 'spoon': 50,
 'bowl': 51,
 'banana': 52,
 'apple': 53,
 'sandwich': 54,
 'orange': 55,
 'broccoli': 56,
 'carrot': 57,
 'hot dog': 58,
 'pizza': 59,
 'donut': 60,
 'cake': 61,
 'chair': 62,
 'couch': 63,
 'potted plant': 64,
 'bed': 65,
 'dining table': 67,
 'toilet': 70,
 'tv': 72,
 'laptop': 73,
 'mouse'

In [35]:
classes = ['__background__'] + categories

In [36]:
num_classes = len(classes)
num_classes

81

In [37]:
json_category_id_to_contiguous_id = {
            v: i + 1 for i, v in enumerate(COCO.getCatIds())}
json_category_id_to_contiguous_id 

{1: 1,
 2: 2,
 3: 3,
 4: 4,
 5: 5,
 6: 6,
 7: 7,
 8: 8,
 9: 9,
 10: 10,
 11: 11,
 13: 12,
 14: 13,
 15: 14,
 16: 15,
 17: 16,
 18: 17,
 19: 18,
 20: 19,
 21: 20,
 22: 21,
 23: 22,
 24: 23,
 25: 24,
 27: 25,
 28: 26,
 31: 27,
 32: 28,
 33: 29,
 34: 30,
 35: 31,
 36: 32,
 37: 33,
 38: 34,
 39: 35,
 40: 36,
 41: 37,
 42: 38,
 43: 39,
 44: 40,
 46: 41,
 47: 42,
 48: 43,
 49: 44,
 50: 45,
 51: 46,
 52: 47,
 53: 48,
 54: 49,
 55: 50,
 56: 51,
 57: 52,
 58: 53,
 59: 54,
 60: 55,
 61: 56,
 62: 57,
 63: 58,
 64: 59,
 65: 60,
 67: 61,
 70: 62,
 72: 63,
 73: 64,
 74: 65,
 75: 66,
 76: 67,
 77: 68,
 78: 69,
 79: 70,
 80: 71,
 81: 72,
 82: 73,
 84: 74,
 85: 75,
 86: 76,
 87: 77,
 88: 78,
 89: 79,
 90: 80}

##  self._init_vcoco()

In [38]:
actions = [x['action_name'] for x in VCOCO]
actions

['hold',
 'stand',
 'sit',
 'ride',
 'walk',
 'look',
 'hit',
 'eat',
 'jump',
 'lay',
 'talk_on_phone',
 'carry',
 'throw',
 'catch',
 'cut',
 'run',
 'work_on_computer',
 'ski',
 'surf',
 'skateboard',
 'smile',
 'drink',
 'kick',
 'point',
 'read',
 'snowboard']

In [39]:
len(actions)

26

In [40]:
roles = [x['role_name'] for x in VCOCO]
roles

[['agent', 'obj'],
 ['agent'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent'],
 ['agent', 'obj'],
 ['agent', 'instr', 'obj'],
 ['agent', 'obj', 'instr'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent', 'obj'],
 ['agent', 'obj'],
 ['agent', 'obj'],
 ['agent', 'instr', 'obj'],
 ['agent'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent'],
 ['agent', 'instr'],
 ['agent', 'obj'],
 ['agent', 'instr'],
 ['agent', 'obj'],
 ['agent', 'instr']]

In [41]:
actions_to_id_map = {v: i for i, v in enumerate(actions)}
actions_to_id_map 

{'hold': 0,
 'stand': 1,
 'sit': 2,
 'ride': 3,
 'walk': 4,
 'look': 5,
 'hit': 6,
 'eat': 7,
 'jump': 8,
 'lay': 9,
 'talk_on_phone': 10,
 'carry': 11,
 'throw': 12,
 'catch': 13,
 'cut': 14,
 'run': 15,
 'work_on_computer': 16,
 'ski': 17,
 'surf': 18,
 'skateboard': 19,
 'smile': 20,
 'drink': 21,
 'kick': 22,
 'point': 23,
 'read': 24,
 'snowboard': 25}

In [42]:
num_actions = len(actions)
num_actions

26

##  def _do_eval(self, detections_file, ovr_thresh=0.5):


### vcocodb = self._get_vcocodb()

In [43]:
vcocodb = copy.deepcopy(COCO.loadImgs(image_ids.tolist()))
len(vcocodb)


4946

In [44]:
vcocodb[0]

{'license': 5,
 'file_name': 'COCO_val2014_000000000294.jpg',
 'coco_url': 'http://images.cocodataset.org/val2014/COCO_val2014_000000000294.jpg',
 'height': 427,
 'width': 640,
 'date_captured': '2013-11-24 05:53:19',
 'flickr_url': 'http://farm4.staticflickr.com/3126/2858898759_4e850a682e_z.jpg',
 'id': 294}

In [45]:
def clip_xyxy_to_image(x1, y1, x2, y2, height, width):
    x1 = np.minimum(width - 1., np.maximum(0., x1))
    y1 = np.minimum(height - 1., np.maximum(0., y1))
    x2 = np.minimum(width - 1., np.maximum(0., x2))
    y2 = np.minimum(height - 1., np.maximum(0., y2))
    return x1, y1, x2, y2
    
def _get_vsrl_data(ann_id, ann_ids, objs):
    """ Get VSRL data for ann_id."""
    action_id = -np.ones((num_actions), dtype=np.int32)
    role_id = -np.ones((num_actions, 2), dtype=np.int32)
    # check if ann_id in vcoco annotations
    in_vcoco = np.where(VCOCO[0]['ann_id'] == ann_id)[0]
    if in_vcoco.size > 0:
        action_id[:] = 0
        role_id[:] = -1
    else:
        return action_id, role_id
    for i, x in enumerate(VCOCO):
        assert x['action_name'] == actions[i]
        has_label = np.where(np.logical_and(x['ann_id'] == ann_id, x['label'] == 1))[0]
        if has_label.size > 0:
            action_id[i] = 1
            assert has_label.size == 1
            rids = x['role_object_id'][has_label]
            assert rids[0, 0] == ann_id
            for j in range(1, rids.shape[1]):
                if rids[0, j] == 0:
                    # no role
                    continue
                aid = np.where(ann_ids == rids[0, j])[0]
                assert aid.size > 0
                role_id[i, j - 1] = aid
    return action_id, role_id
def _prep_vcocodb_entry(entry):
    entry['boxes'] = np.empty((0, 4), dtype=np.float32)
    entry['is_crowd'] = np.empty((0), dtype=np.bool)
    entry['gt_classes'] = np.empty((0), dtype=np.int32)
    entry['gt_actions'] = np.empty((0, num_actions), dtype=np.int32)
    entry['gt_role_id'] = np.empty((0, num_actions, 2), dtype=np.int32)
def _add_gt_annotations(entry):
    ann_ids = COCO.getAnnIds(imgIds=entry['id'], iscrowd=None)
    objs = COCO.loadAnns(ann_ids)
    # Sanitize bboxes -- some are invalid
    valid_objs = []
    valid_ann_ids = []
    width = entry['width']
    height = entry['height']
    for i, obj in enumerate(objs):
        if 'ignore' in obj and obj['ignore'] == 1:
            continue
        # Convert form x1, y1, w, h to x1, y1, x2, y2
        x1 = obj['bbox'][0]
        y1 = obj['bbox'][1]
        x2 = x1 + np.maximum(0., obj['bbox'][2] - 1.)
        y2 = y1 + np.maximum(0., obj['bbox'][3] - 1.)
        x1, y1, x2, y2 = clip_xyxy_to_image(
            x1, y1, x2, y2, height, width)
        # Require non-zero seg area and more than 1x1 box size
        if obj['area'] > 0 and x2 > x1 and y2 > y1:
            obj['clean_bbox'] = [x1, y1, x2, y2]
            valid_objs.append(obj)
            valid_ann_ids.append(ann_ids[i])
    num_valid_objs = len(valid_objs)
    assert num_valid_objs == len(valid_ann_ids)

    boxes = np.zeros((num_valid_objs, 4), dtype=entry['boxes'].dtype)
    is_crowd = np.zeros((num_valid_objs), dtype=entry['is_crowd'].dtype)
    gt_classes = np.zeros((num_valid_objs), dtype=entry['gt_classes'].dtype)
    gt_actions = -np.ones((num_valid_objs, num_actions), dtype=entry['gt_actions'].dtype)
    gt_role_id = -np.ones((num_valid_objs, num_actions, 2), dtype=entry['gt_role_id'].dtype)

    for ix, obj in enumerate(valid_objs):
        cls = json_category_id_to_contiguous_id[obj['category_id']]
        boxes[ix, :] = obj['clean_bbox']
        gt_classes[ix] = cls
        is_crowd[ix] = obj['iscrowd']

        gt_actions[ix, :], gt_role_id[ix, :, :] = \
            _get_vsrl_data(valid_ann_ids[ix],
                                valid_ann_ids, valid_objs)

    entry['boxes'] = np.append(entry['boxes'], boxes, axis=0)
    entry['gt_classes'] = np.append(entry['gt_classes'], gt_classes)
    entry['is_crowd'] = np.append(entry['is_crowd'], is_crowd)
    entry['gt_actions'] = np.append(entry['gt_actions'], gt_actions, axis=0)
    entry['gt_role_id'] = np.append(entry['gt_role_id'], gt_role_id, axis=0)

In [46]:
for entry in vcocodb:
    _prep_vcocodb_entry(entry)
    _add_gt_annotations(entry)

In [47]:
len(vcocodb)

4946

##  划重点，最终要计算map的文件，一个是通过三个文件预处理生成的vcocodb，一个是网络预测得到的pkl，

## 下面分析vcocodb

In [48]:
vcocodb[1]

{'license': 1,
 'file_name': 'COCO_val2014_000000000328.jpg',
 'coco_url': 'http://images.cocodataset.org/val2014/COCO_val2014_000000000328.jpg',
 'height': 491,
 'width': 640,
 'date_captured': '2013-11-16 13:07:51',
 'flickr_url': 'http://farm3.staticflickr.com/2813/9198207893_5f31aaa152_z.jpg',
 'id': 328,
 'boxes': array([[434.75, 283.15, 468.76, 300.79],
        [ 44.81,  68.09, 267.61, 424.  ],
        [197.91,  90.52, 402.04, 478.86],
        [336.87,  58.48, 585.78, 483.52],
        [  0.6 , 104.76, 587.27, 478.5 ],
        [245.65, 220.95, 331.09, 257.37],
        [350.46,  77.31, 450.48, 141.92],
        [462.06, 177.54, 479.37, 220.35],
        [315.37, 171.71, 336.87, 228.69],
        [ 12.03, 171.36, 130.48, 249.99],
        [ 49.45, 160.85, 133.73, 207.69]], dtype=float32),
 'is_crowd': array([False, False, False, False, False, False, False, False, False,
        False, False]),
 'gt_classes': array([68,  1,  1,  1, 14, 74,  3, 28, 28, 25, 25], dtype=int32),
 'gt_actions'

In [49]:
vcocodb[0].keys()

dict_keys(['license', 'file_name', 'coco_url', 'height', 'width', 'date_captured', 'flickr_url', 'id', 'boxes', 'is_crowd', 'gt_classes', 'gt_actions', 'gt_role_id'])

In [50]:
vcocodb[12]

{'license': 4,
 'file_name': 'COCO_val2014_000000001180.jpg',
 'coco_url': 'http://images.cocodataset.org/val2014/COCO_val2014_000000001180.jpg',
 'height': 640,
 'width': 426,
 'date_captured': '2013-11-17 06:06:35',
 'flickr_url': 'http://farm1.staticflickr.com/66/194967296_38bf7abb48_z.jpg',
 'id': 1180,
 'boxes': array([[324.57, 284.03, 398.73, 394.96],
        [301.09, 278.64, 333.49, 329.97],
        [134.05, 118.2 , 303.14, 419.9 ],
        [  0.  , 248.38,  49.58, 463.77],
        [176.14, 415.23, 186.59, 424.33],
        [ 62.24, 485.78, 174.16, 536.21],
        [162.09, 401.41, 413.67, 498.24],
        [346.43, 468.6 , 424.96, 482.43],
        [  0.  , 395.51, 425.  , 631.81],
        [ 31.96, 238.66, 120.27, 437.97],
        [371.44, 226.55, 424.45, 387.56],
        [ 77.98, 494.96,  99.73, 508.59],
        [144.15, 501.22, 164.58, 505.91],
        [118.69, 302.1 , 126.79, 343.7 ],
        [403.59, 335.8 , 414.44, 386.81],
        [  2.37, 387.79,  13.21, 397.6 ],
        [1

In [51]:
vcocodb[0]['gt_role_id']vcocodb[0]['boxes'].shape

(20, 4)

In [52]:
vcocodb[0]['is_crowd'].shape

(20,)

In [53]:
vcocodb[0]['gt_classes'].shape

(20,)

In [54]:
vcocodb[0]['gt_actions'].shape

(20, 26)

In [55]:
vcocodb[5]['gt_role_id'].shape

(17, 26, 2)

In [56]:
vcocodb[1]

{'license': 1,
 'file_name': 'COCO_val2014_000000000328.jpg',
 'coco_url': 'http://images.cocodataset.org/val2014/COCO_val2014_000000000328.jpg',
 'height': 491,
 'width': 640,
 'date_captured': '2013-11-16 13:07:51',
 'flickr_url': 'http://farm3.staticflickr.com/2813/9198207893_5f31aaa152_z.jpg',
 'id': 328,
 'boxes': array([[434.75, 283.15, 468.76, 300.79],
        [ 44.81,  68.09, 267.61, 424.  ],
        [197.91,  90.52, 402.04, 478.86],
        [336.87,  58.48, 585.78, 483.52],
        [  0.6 , 104.76, 587.27, 478.5 ],
        [245.65, 220.95, 331.09, 257.37],
        [350.46,  77.31, 450.48, 141.92],
        [462.06, 177.54, 479.37, 220.35],
        [315.37, 171.71, 336.87, 228.69],
        [ 12.03, 171.36, 130.48, 249.99],
        [ 49.45, 160.85, 133.73, 207.69]], dtype=float32),
 'is_crowd': array([False, False, False, False, False, False, False, False, False,
        False, False]),
 'gt_classes': array([68,  1,  1,  1, 14, 74,  3, 28, 28, 25, 25], dtype=int32),
 'gt_actions'

In [57]:
gt_inds = np.where(vcocodb[0]['gt_classes'] == 1)[0]
            # person boxes
gt_boxes = vcocodb[0]['boxes'][gt_inds]
gt_actions = vcocodb[0]['gt_actions'][gt_inds]

In [58]:
gt_actions

array([[0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 1, 0, 0]], dtype=int32)

In [59]:
ignore = np.any(gt_actions == -1, axis=1)

In [60]:
ignore

array([False])

In [61]:
a=[]
for i in range(len(vcocodb)):
    image_id = vcocodb[i]['id']  # len<6
    gt_inds = np.where(vcocodb[i]['gt_classes'] == 1)[0]
    # person boxes
    gt_boxes = vcocodb[i]['boxes'][gt_inds]
    gt_actions = vcocodb[i]['gt_actions'][gt_inds]
    # some peorson instances don't have annotated actions
    # we ignore those instances
    ignore = np.any(gt_actions == -1, axis=1)
    if image_id==395:
        print(i)
    if np.any(ignore):
        
        a.append(image_id)

2


In [72]:
vcocodb

[{'license': 5,
  'file_name': 'COCO_val2014_000000000294.jpg',
  'coco_url': 'http://images.cocodataset.org/val2014/COCO_val2014_000000000294.jpg',
  'height': 427,
  'width': 640,
  'date_captured': '2013-11-24 05:53:19',
  'flickr_url': 'http://farm4.staticflickr.com/3126/2858898759_4e850a682e_z.jpg',
  'id': 294,
  'boxes': array([[2.7700e+01, 6.9830e+01, 3.9161e+02, 4.2600e+02],
         [4.1557e+02, 3.4985e+02, 4.2988e+02, 3.7240e+02],
         [5.0760e+02, 3.1281e+02, 6.3806e+02, 4.2120e+02],
         [6.0851e+02, 2.5183e+02, 6.1518e+02, 2.9158e+02],
         [4.4573e+02, 3.2905e+02, 4.6206e+02, 3.6272e+02],
         [4.5437e+02, 3.2069e+02, 4.6926e+02, 3.6486e+02],
         [4.0149e+02, 3.2329e+02, 4.2359e+02, 3.4761e+02],
         [3.8389e+02, 3.4186e+02, 4.1847e+02, 3.8090e+02],
         [4.0219e+02, 1.1167e+02, 4.1566e+02, 2.2533e+02],
         [4.2095e+02, 1.1440e+02, 4.3338e+02, 2.1667e+02],
         [3.2899e+02, 2.5648e+02, 3.4616e+02, 3.2241e+02],
         [4.6160e+02, 3

In [63]:
npos = np.zeros((26), dtype=np.float32)

In [64]:
for aid in range(26):
    npos[aid] += np.sum(gt_actions[:, aid] == 1)

In [65]:
npos

array([0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 1., 0., 0., 0., 0., 0., 0.], dtype=float32)

In [66]:
detections_file='/root/gudongzhou/PPDM0102V2.0/src/gdz_util/anno/gdz_vcoco_test_scores.pkl'
with open(detections_file, 'rb') as f:
    dets = pickle.load(f)

In [67]:
image_id = vcocodb[1]['id'] 

In [68]:
num_actions

26

In [69]:
def _collect_detections_for_image(dets, image_id):
    agents = np.empty((0, 4 + 26), dtype=np.float32)
    roles = np.empty((0, 5 * 26, 2), dtype=np.float32)
    for det in dets:
        if str(det['image_id']).zfill(6) == str(image_id).zfill(6):

            this_agent = np.zeros((1, 4 + 26), dtype=np.float32)
            this_role = np.zeros((1, 5 * 26, 2), dtype=np.float32)
            this_agent[0, :4] = det['person_box']
            for aid in range(26):
                for j, rid in enumerate(roles[aid]):
                    if rid == 'agent':
                        this_agent[0, 4 + aid] = det[actions[aid] + '_' + rid]
                    else:
                        this_role[0, 5 * aid: 5 * aid + 5, j - 1] = det[actions[aid] + '_' + rid]
            agents = np.concatenate((agents, this_agent), axis=0)  # N*(4+26)
            roles = np.concatenate((roles, this_role), axis=0)  # N*(5*26)*2
    return agents, roles

In [70]:
pred_agents, pred_roles = _collect_detections_for_image(dets, image_id)

IndexError: index 0 is out of bounds for axis 0 with size 0

In [ ]:
import json, os
import numpy as np


class MyEncoder(json.JSONEncoder):
    def default(self, obj):
        if isinstance(obj, np.integer):
            return int(obj)
        elif isinstance(obj, np.uint8):
            return int(obj)
        elif isinstance(obj, np.floating):
            return float(obj)
        elif isinstance(obj, np.ndarray):
            return obj.tolist()
        else:
            return super(MyEncoder, self).default(obj)


def save_json(annot_file, filename):
    with open(filename, 'w') as outfile:
        outfile.write(json.dumps(annot_file, cls=MyEncoder))
    

In [ ]:
vcocodb[0]

In [ ]:
save_path = '/root/Documents/test1.json'

save_json(vcocodb[0],save_path)

In [77]:
vcocodb[0]['boxes']=np.array([[102.27868852459017, 24.065573770491795, 285.88524590163934, 269.9672131147541],[80.9672131147541,100.29508196721312,331.78688524590166,321.60655737704917]])

In [78]:
vcocodb[0]['boxes']

array([[102.27868852,  24.06557377, 285.8852459 , 269.96721311],
       [ 80.96721311, 100.29508197, 331.78688525, 321.60655738]])

In [80]:
vcocodb[0]['file_name']='1.jpg'

In [82]:
vcocodb[0]['gt_classes']=np.array([1,18])

In [83]:
vcocodb[0].['gt_actions']=np.array([[0,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
          0,  0,  0,  0,  0,  0,  0,  1,  0,  0]])

{'license': 5,
 'file_name': '1.jpg',
 'coco_url': 'http://images.cocodataset.org/val2014/COCO_val2014_000000000294.jpg',
 'height': 427,
 'width': 640,
 'date_captured': '2013-11-24 05:53:19',
 'flickr_url': 'http://farm4.staticflickr.com/3126/2858898759_4e850a682e_z.jpg',
 'id': 294,
 'boxes': array([[102.27868852,  24.06557377, 285.8852459 , 269.96721311],
        [ 80.96721311, 100.29508197, 331.78688525, 321.60655738]]),
 'is_crowd': array([False, False, False, False, False, False, False, False, False,
        False, False, False, False, False, False, False, False, False,
        False, False]),
 'gt_classes': array([ 1, 18]),
 'gt_actions': array([[ 0,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
          0,  0,  0,  0,  0,  0,  0,  1,  0,  0],
        [-1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1,
         -1, -1, -1, -1, -1, -1, -1, -1, -1, -1],
        [-1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1,
         -1, -1, -1, -1, -1

In [83]:
vcocodb[0].['']

{'license': 5,
 'file_name': '1.jpg',
 'coco_url': 'http://images.cocodataset.org/val2014/COCO_val2014_000000000294.jpg',
 'height': 427,
 'width': 640,
 'date_captured': '2013-11-24 05:53:19',
 'flickr_url': 'http://farm4.staticflickr.com/3126/2858898759_4e850a682e_z.jpg',
 'id': 294,
 'boxes': array([[102.27868852,  24.06557377, 285.8852459 , 269.96721311],
        [ 80.96721311, 100.29508197, 331.78688525, 321.60655738]]),
 'is_crowd': array([False, False, False, False, False, False, False, False, False,
        False, False, False, False, False, False, False, False, False,
        False, False]),
 'gt_classes': array([ 1, 18]),
 'gt_actions': array([[ 0,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
          0,  0,  0,  0,  0,  0,  0,  1,  0,  0],
        [-1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1,
         -1, -1, -1, -1, -1, -1, -1, -1, -1, -1],
        [-1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1,
         -1, -1, -1, -1, -1

In [86]:
print('Actions', actions)

Actions ['hold', 'stand', 'sit', 'ride', 'walk', 'look', 'hit', 'eat', 'jump', 'lay', 'talk_on_phone', 'carry', 'throw', 'catch', 'cut', 'run', 'work_on_computer', 'ski', 'surf', 'skateboard', 'smile', 'drink', 'kick', 'point', 'read', 'snowboard']


In [87]:
actions_to_id_map

{'hold': 0,
 'stand': 1,
 'sit': 2,
 'ride': 3,
 'walk': 4,
 'look': 5,
 'hit': 6,
 'eat': 7,
 'jump': 8,
 'lay': 9,
 'talk_on_phone': 10,
 'carry': 11,
 'throw': 12,
 'catch': 13,
 'cut': 14,
 'run': 15,
 'work_on_computer': 16,
 'ski': 17,
 'surf': 18,
 'skateboard': 19,
 'smile': 20,
 'drink': 21,
 'kick': 22,
 'point': 23,
 'read': 24,
 'snowboard': 25}

In [89]:
len(roles)

26

In [91]:
vcocodb[0]['gt_role_id']

array([[[-1, -1],
        [-1, -1],
        [-1, -1],
        ...,
        [-1, -1],
        [-1, -1],
        [-1, -1]],

       [[-1, -1],
        [-1, -1],
        [-1, -1],
        ...,
        [-1, -1],
        [-1, -1],
        [-1, -1]],

       [[-1, -1],
        [-1, -1],
        [-1, -1],
        ...,
        [-1, -1],
        [-1, -1],
        [-1, -1]],

       ...,

       [[-1, -1],
        [-1, -1],
        [-1, -1],
        ...,
        [-1, -1],
        [-1, -1],
        [-1, -1]],

       [[-1, -1],
        [-1, -1],
        [-1, -1],
        ...,
        [-1, -1],
        [-1, -1],
        [-1, -1]],

       [[-1, -1],
        [-1, -1],
        [-1, -1],
        ...,
        [-1, -1],
        [-1, -1],
        [-1, -1]]], dtype=int32)

In [93]:
roles

[['agent', 'obj'],
 ['agent'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent'],
 ['agent', 'obj'],
 ['agent', 'instr', 'obj'],
 ['agent', 'obj', 'instr'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent', 'obj'],
 ['agent', 'obj'],
 ['agent', 'obj'],
 ['agent', 'instr', 'obj'],
 ['agent'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent', 'instr'],
 ['agent'],
 ['agent', 'instr'],
 ['agent', 'obj'],
 ['agent', 'instr'],
 ['agent', 'obj'],
 ['agent', 'instr']]

In [94]:
rid=roles[1]

In [95]:
rid

['agent']

In [98]:
len(rid)

1

In [99]:
a=[[1,2]]

In [100]:
a.shaoe

AttributeError: 'list' object has no attribute 'shaoe'

In [101]:
a.shape

AttributeError: 'list' object has no attribute 'shape'

In [102]:
VCOCO

[{'image_id': array([[ 45687],
         [209468],
         [293221],
         ...,
         [222468],
         [450845],
         [515854]]),
  'ann_id': array([[ 183014],
         [ 183062],
         [ 183100],
         ...,
         [2229301],
         [2229367],
         [2229495]]),
  'role_object_id': array([[ 183014,       0],
         [ 183062,       0],
         [ 183100, 2112209],
         ...,
         [2229301,       0],
         [2229367,  629756],
         [2229495,       0]]),
  'label': array([[0],
         [0],
         [1],
         ...,
         [0],
         [1],
         [1]]),
  'action_name': 'hold',
  'role_name': ['agent', 'obj'],
  'include': [[], []]},
 {'image_id': array([[ 45687],
         [209468],
         [293221],
         ...,
         [222468],
         [450845],
         [515854]]),
  'ann_id': array([[ 183014],
         [ 183062],
         [ 183100],
         ...,
         [2229301],
         [2229367],
         [2229495]]),
  'role_object_id': array

In [103]:
x=VCOCO[0]

In [107]:
rids=x['role_object_id'][0]

In [111]:
has_label = np.where(x['label'] == 1)[0]
has_label

array([   2,    5,    6, ..., 7761, 7766, 7767])

In [114]:
rids = x['role_object_id'][has_label]
rids

array([[ 183100, 2112209],
       [ 183209,       0],
       [ 183263,   56789],
       ...,
       [2228880,  302609],
       [2229367,  629756],
       [2229495,       0]])

In [118]:
rids[1,0]

183209

In [116]:
rids.shape

(3608, 2)

In [117]:
rids[0, 1] 

2112209